In [ ]:
!pip3 install praw

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 191.0/191.0 kB 4.1 MB/s eta 0:00:00


In [ ]:
#DATA EXTRACTION
import praw
import pandas as pd
from datetime import datetime, timedelta
from google.colab import files
import time
reddit = praw.Reddit(
    client_id='vgG7u7zkyftNgK77U8UVPg',
    client_secret='2v-U0DeDJawVSu5CByMR2UHlgeUSpA',
    user_agent='Toxic Behavior Analysis'
)

subreddit_name = 'VALORANT'
subreddit = reddit.subreddit(subreddit_name)

data = {
    "ID": [], "Author": [], "Type": [], "Title": [], "Text": [], "Score": [],
    "Parent_Name": [], "Community URL": [], "Date": [], "Time": [], "Submission id": [], "Post URL": []
}

def get_date_time(timestamp):
    dt = datetime.fromtimestamp(timestamp)
    return dt.date(), dt.time()

def fetch_top_posts(subreddit, limit, time_filter='year'):
    return list(subreddit.top(time_filter=time_filter, limit=limit))

total_count = 0
batch_size = 1000
retry_attempts = 5
current_time = datetime.now().strftime('%Y-%m-%d_%H-%M-%S')

while total_count < 25000:
    for attempt in range(retry_attempts):
        try:
            posts = fetch_top_posts(subreddit, batch_size)
            break
        except praw.exceptions.APIException as e:
            if e.error_type == 'RATELIMIT':
                sleep_time = int(re.search(r'\d+', str(e)).group())
                print(f"Rate limit hit. Sleeping for {sleep_time} seconds.")
                time.sleep(sleep_time)
            else:
                print(f"Error fetching posts: {e}")
                time.sleep(5)
        except Exception as e:
            print(f"Error fetching posts: {e}")
            time.sleep(5)
    else:
        print("Max retries reached. Exiting.")
        break

    for post in posts:
        try:
            submission = reddit.submission(id=post.id)
            submission.comments.replace_more(limit=None)
            print(f"Fetching posts. Total count: {total_count}")


            post_date, post_time = get_date_time(submission.created_utc)
            data["ID"].append(submission.id)
            data["Author"].append(submission.author.name if submission.author else "[deleted]")
            data["Type"].append("Post")
            data["Title"].append(submission.title)
            data["Text"].append(submission.selftext)
            data["Score"].append(submission.score)
            data["Parent_Name"].append(None)
            data["Community URL"].append(submission.subreddit.url)
            data["Date"].append(post_date)
            data["Time"].append(post_time)
            data["Submission id"].append(submission.id)
            data["Post URL"].append(submission.url)
            total_count += 1


            for comment in submission.comments.list():
                if total_count >= 25000:
                    break

                comment_date, comment_time = get_date_time(comment.created_utc)
                data["ID"].append(comment.id)
                data["Author"].append(comment.author.name if comment.author else "[deleted]")
                data["Type"].append("Comment")
                data["Title"].append(None)
                data["Text"].append(comment.body)
                data["Score"].append(comment.score)
                if comment.parent_id != submission.id:
                    data["Parent_Name"].append(comment.parent().author.name if comment.parent().author else None)
                else:
                    data["Parent_Name"].append(submission.author.name if submission.author else None)
                data["Community URL"].append(submission.subreddit.url)
                data["Date"].append(comment_date)
                data["Time"].append(comment_time)
                data["Submission id"].append(comment.link_id)
                data["Post URL"].append(submission.url)
                total_count += 1
                print(f"Fetching posts. Total count: {total_count}")


                for reply in comment.replies:
                    if total_count >= 25000:
                        break

                    reply_date, reply_time = get_date_time(reply.created_utc)
                    data["ID"].append(reply.id)
                    data["Author"].append(reply.author.name if reply.author else "[deleted]")
                    data["Type"].append("Reply")
                    data["Title"].append(None)
                    data["Text"].append(reply.body)
                    data["Score"].append(reply.score)
                    data["Parent_Name"].append(comment.author.name if comment.author else None)
                    data["Community URL"].append(submission.subreddit.url)
                    data["Date"].append(reply_date)
                    data["Time"].append(reply_time)
                    data["Submission id"].append(reply.link_id)
                    data["Post URL"].append(submission.url)
                    total_count += 1
                    print(f"Fetching posts. Total count: {total_count}")

            if total_count >= 25000:
                break

        except Exception as e:
            print(f"Error processing post {post.id}: {e}")
            time.sleep(2)

    if total_count % 5000 == 0 or total_count >= 25000:
        df = pd.DataFrame(data)
        excel_filename = f"VALORANT_data_{total_count}.xlsx"
        try:
            with pd.ExcelWriter(excel_filename, engine='openpyxl') as writer:
                df.to_excel(writer, sheet_name='Posts_and_Comments', index=False)

                workbook = writer.book
                sheet = workbook['Posts_and_Comments']
                for column in sheet.columns:
                    max_length = 0
                    column_letter = column[0].column_letter
                    for cell in column:
                        try:
                            if len(str(cell.value)) > max_length:
                                max_length = len(cell.value)
                        except:
                            pass
                    adjusted_width = max_length + 2
                    sheet.column_dimensions[column_letter].width = adjusted_width

            print(f"Data saved to {excel_filename}")
            files.download(excel_filename)

        except Exception as e:
            print(f"Error saving data to Excel: {e}")
    time.sleep(1)

print("Data extraction completed.")


It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/l

Fetching posts. Total count: 0
Fetching posts. Total count: 2
Fetching posts. Total count: 3
Fetching posts. Total count: 4
Fetching posts. Total count: 5
Fetching posts. Total count: 6
Fetching posts. Total count: 7
Fetching posts. Total count: 8
Fetching posts. Total count: 9
Fetching posts. Total count: 10
Fetching posts. Total count: 11
Fetching posts. Total count: 12
Fetching posts. Total count: 13
Fetching posts. Total count: 14
Fetching posts. Total count: 15
Fetching posts. Total count: 16
Fetching posts. Total count: 17
Fetching posts. Total count: 18
Fetching posts. Total count: 19
Fetching posts. Total count: 20
Fetching posts. Total count: 21
Fetching posts. Total count: 22
Fetching posts. Total count: 23
Fetching posts. Total count: 24
Fetching posts. Total count: 25
Fetching posts. Total count: 26
Fetching posts. Total count: 27
Fetching posts. Total count: 28
Fetching posts. Total count: 29
Fetching posts. Total count: 30
Fetching posts. Total count: 31
Fetching posts. T

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.




Fetching posts. Total count: 4076
Fetching posts. Total count: 4077
Fetching posts. Total count: 4078
Fetching posts. Total count: 4079
Fetching posts. Total count: 4080
Fetching posts. Total count: 4081
Fetching posts. Total count: 4082
Fetching posts. Total count: 4083
Fetching posts. Total count: 4084
Fetching posts. Total count: 4085
Fetching posts. Total count: 4086
Fetching posts. Total count: 4087
Fetching posts. Total count: 4088
Fetching posts. Total count: 4089
Fetching posts. Total count: 4090
Fetching posts. Total count: 4091
Fetching posts. Total count: 4092
Fetching posts. Total count: 4093
Fetching posts. Total count: 4094
Fetching posts. Total count: 4095
Fetching posts. Total count: 4096
Fetching posts. Total count: 4097
Fetching posts. Total count: 4098
Fetching posts. Total count: 4099
Fetching posts. Total count: 4100
Fetching posts. Total count: 4101
Fetching posts. Total count: 4102
Fetching posts. Total count: 4103
Fetching posts. Total count: 4104
Fetching post

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.



...

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/latest/getting_started/multiple_instances.html#discord-bots-and-asynchronous-environments for more info.

It is strongly recommended to use Async PRAW: https://asyncpraw.readthedocs.io.
See https://praw.readthedocs.io/en/l

Fetching posts. Total count: 23644
Fetching posts. Total count: 23646
Fetching posts. Total count: 23647
Fetching posts. Total count: 23648
Fetching posts. Total count: 23649
Fetching posts. Total count: 23650
Fetching posts. Total count: 23651
Fetching posts. Total count: 23652
Fetching posts. Total count: 23653
Fetching posts. Total count: 23654
Fetching posts. Total count: 23655
Fetching posts. Total count: 23656
Fetching posts. Total count: 23657
Fetching posts. Total count: 23658
Fetching posts. Total count: 23659
Fetching posts. Total count: 23660
Fetching posts. Total count: 23661
Fetching posts. Total count: 23662
Fetching posts. Total count: 23663
Fetching posts. Total count: 23664
Fetching posts. Total count: 23665
Fetching posts. Total count: 23666
Fetching posts. Total count: 23667
Fetching posts. Total count: 23668
Fetching posts. Total count: 23669
Fetching posts. Total count: 23670
Fetching posts. Total count: 23671
Fetching posts. Total count: 23672
Fetching posts. Tota

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Data extraction completed.


In [ ]:
#DATA CLEANING
!pip install pandas openpyxl
!pip install pyLDAvis

import pandas as pd
df = pd.read_excel('/content/CombinedCommentsAndReplies.xlsx')

#Replacing deleted and removed comments with null
df['Text'] = df['Text'].replace(['[deleted]', '[removed]'], pd.NA)

#Dropping all null values
df = df.dropna(subset=['Text'])

#Lowercasing the text
df['Text'] = df['Text'].str.lower()

#Removing URLs
import re
df['Text'] = df['Text'].apply(lambda x: re.sub(r'http\S+|www\S+', '', x))

#Remove Special Characters and keep only necessary punctuations and emojis
df['Text'] = df['Text'].apply(lambda x: re.sub(r'[^A-Za-z0-9\s.,!?\'\"-]', '', x))

#Remove HTML Tags
df['Text'] = df['Text'].apply(lambda x: re.sub(r'<[^>]+>', '', x))

#Remove stop words
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')
stop_words = set(stopwords.words('english'))
df['Text'] = df['Text'].apply(lambda x: ' '.join([word for word in x.split() if word not in stop_words]))

#Tokenization and Lemmatization
import nltk
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
nltk.download('punkt')
nltk.download('wordnet')
lemmatizer = WordNetLemmatizer()
df['Text'] = df['Text'].apply(lambda x: ' '.join([lemmatizer.lemmatize(word) for word in word_tokenize(x)]))

#Handling repeated characters
df['Text'] = df['Text'].apply(lambda x: re.sub(r'(.)\1+', r'\1\1', x))

#Removing negations
df['Text'] = df['Text'].apply(lambda x: re.sub(r"\b(not|no|never|n't)\b", lambda match: match.group(0) + '_', x))

sentimentAnalysisDf = df

df.head()
df.shape

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


(73251, 12)

In [ ]:
#Topic modelling
import gensim
from gensim.utils import simple_preprocess
from gensim import corpora
from gensim.models.ldamodel import LdaModel
import pyLDAvis.gensim_models

# Tokenization function
def tokenize(text):
    return simple_preprocess(text, deacc=False)

# Apply tokenization to the 'Text' column
df['tokenized_text'] = df['Text'].apply(tokenize)

# Create a dictionary
dictionary = corpora.Dictionary(df['tokenized_text'])
dictionary.filter_extremes(no_below=5, no_above=0.5)

# Create a Bag of Words corpus
corpus = [dictionary.doc2bow(text) for text in df['tokenized_text']]

num_topics = 5

# LDA model
lda_model = LdaModel(corpus=corpus,
                     id2word=dictionary,
                     num_topics=num_topics,
                     random_state=100,
                     update_every=1,
                     chunksize=100,
                     passes=10,
                     alpha='auto',
                     per_word_topics=True)

# Print the topics
topics = lda_model.print_topics(num_words=5)
for idx, topic in topics:
    print(f"Topic {idx + 1}: {topic}")


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


Topic 1: 0.046*"game" + 0.021*"back" + 0.016*"thing" + 0.016*"play" + 0.015*"na"
Topic 2: 0.036*"time" + 0.032*"team" + 0.026*"day" + 0.022*"make" + 0.018*"new"
Topic 3: 0.031*"year" + 0.025*"hero" + 0.020*"even" + 0.020*"last" + 0.017*"right"
Topic 4: 0.044*"like" + 0.025*"get" + 0.021*"would" + 0.020*"think" + 0.017*"people"
Topic 5: 0.095*"ti" + 0.042*"one" + 0.024*"mana" + 0.023*"got" + 0.021*"much"


In [ ]:
import pyLDAvis.gensim_models

lda_display= pyLDAvis.gensim_models.prepare(lda_model, corpus, dictionary, sort_topics=False, mds='mmds')
pyLDAvis.display(lda_display)

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)
/usr/local/lib/python3.10/dist-packages/sklearn/manifold/_mds.py:298: FutureWarning: The default value of `normalized_stress` will change to `'auto'` in version 1.4. To suppress this warning, manually set the value of `normalized_stress`.
  warnings.warn(


In [ ]:
#NETWORK ANALYSIS for Valorant
import networkx as nx

G = nx.DiGraph()
for _, row in df.iterrows():
    if row['Community URL'] == '/r/VALORANT/' and (row['Type'] == 'Comment' or row['Type'] == 'Reply'):
        author = str(row['Author'])
        parent_author = str(row['Parent_Name'])
        if parent_author and parent_author != author:
            G.add_edge(author, parent_author)
print(f"Number of nodes: {G.number_of_nodes()}")
print(f"Number of edges: {G.number_of_edges()}")

from networkx.algorithms.community import greedy_modularity_communities

communities = list(greedy_modularity_communities(G))

community_dict = {}
for i, community in enumerate(communities):
    for node in community:
        community_dict[node] = i

nx.set_node_attributes(G, community_dict, 'community')

import plotly.graph_objects as go

pos = nx.spring_layout(G)
edge_x = []
edge_y = []
for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_x.append(x0)
    edge_x.append(x1)
    edge_x.append(None)
    edge_y.append(y0)
    edge_y.append(y1)
    edge_y.append(None)

edge_trace = go.Scatter(
    x=edge_x, y=edge_y,
    line=dict(width=0.5, color='#888'),
    hoverinfo='none',
    mode='lines'
)
node_x = []
node_y = []
node_text = []
node_color = []
for node in G.nodes():
    x, y = pos[node]
    node_x.append(x)
    node_y.append(y)
    node_text.append(node)
    node_color.append(community_dict[node])

node_trace = go.Scatter(
    x=node_x, y=node_y,
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        colorscale='Viridis',
        color=node_color,
        size=10,
        colorbar=dict(
            thickness=15,
            title='Community',
            xanchor='left',
            titleside='right'
        ),
        line_width=2
    )
)
node_trace.text = node_text
fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                title='Network graph of Reddit interactions for VALORANT<br>',
                titlefont_size=16,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20, l=5, r=5, t=40),
                xaxis=dict(showgrid=False, zeroline=False),
                yaxis=dict(showgrid=False, zeroline=False)
             )
)

fig.show()

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning:

`should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.



Number of nodes: 7761
Number of edges: 13636


In [ ]:
#NETWORK ANALYSIS for NomadOfNowhere
import networkx as nx

G = nx.DiGraph()
for _, row in df.iterrows():
    if row['Community URL'] == '/r/NomadOfNowhere/' and (row['Type'] == 'Comment' or row['Type'] == 'Reply'):
        author = str(row['Author'])
        parent_author = str(row['Parent_Name'])
        if parent_author and parent_author != author:
            G.add_edge(author, parent_author)
print(f"Number of nodes: {G.number_of_nodes()}")
print(f"Number of edges: {G.number_of_edges()}")

from networkx.algorithms.community import greedy_modularity_communities

communities = list(greedy_modularity_communities(G))

community_dict = {}
for i, community in enumerate(communities):
    for node in community:
        community_dict[node] = i

nx.set_node_attributes(G, community_dict, 'community')

import plotly.graph_objects as go

pos = nx.spring_layout(G)
edge_x = []
edge_y = []
for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_x.append(x0)
    edge_x.append(x1)
    edge_x.append(None)
    edge_y.append(y0)
    edge_y.append(y1)
    edge_y.append(None)

edge_trace = go.Scatter(
    x=edge_x, y=edge_y,
    line=dict(width=0.5, color='#888'),
    hoverinfo='none',
    mode='lines'
)
node_x = []
node_y = []
node_text = []
node_color = []
for node in G.nodes():
    x, y = pos[node]
    node_x.append(x)
    node_y.append(y)
    node_text.append(node)
    node_color.append(community_dict[node])

node_trace = go.Scatter(
    x=node_x, y=node_y,
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        colorscale='Viridis',
        color=node_color,
        size=10,
        colorbar=dict(
            thickness=15,
            title='Community',
            xanchor='left',
            titleside='right'
        ),
        line_width=2
    )
)
node_trace.text = node_text
fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                title='Network graph of Reddit interactions for Nomad Of NOwhere<br>',
                titlefont_size=16,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20, l=5, r=5, t=40),
                xaxis=dict(showgrid=False, zeroline=False),
                yaxis=dict(showgrid=False, zeroline=False)
             )
)

fig.show()

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning:

`should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.



Number of nodes: 4387
Number of edges: 12785


In [ ]:
#NETWORK ANALYSIS for BlackBoxDown
import networkx as nx

G = nx.DiGraph()
for _, row in df.iterrows():
    if row['Community URL'] == '/r/BlackBoxDown/' and (row['Type'] == 'Comment' or row['Type'] == 'Reply'):
        author = str(row['Author'])
        parent_author = str(row['Parent_Name'])
        if parent_author and parent_author != author:
            G.add_edge(author, parent_author)
print(f"Number of nodes: {G.number_of_nodes()}")
print(f"Number of edges: {G.number_of_edges()}")

from networkx.algorithms.community import greedy_modularity_communities

communities = list(greedy_modularity_communities(G))

community_dict = {}
for i, community in enumerate(communities):
    for node in community:
        community_dict[node] = i

nx.set_node_attributes(G, community_dict, 'community')

import plotly.graph_objects as go

pos = nx.spring_layout(G)
edge_x = []
edge_y = []
for edge in G.edges():
    x0, y0 = pos[edge[0]]
    x1, y1 = pos[edge[1]]
    edge_x.append(x0)
    edge_x.append(x1)
    edge_x.append(None)
    edge_y.append(y0)
    edge_y.append(y1)
    edge_y.append(None)

edge_trace = go.Scatter(
    x=edge_x, y=edge_y,
    line=dict(width=0.5, color='#888'),
    hoverinfo='none',
    mode='lines'
)
node_x = []
node_y = []
node_text = []
node_color = []
for node in G.nodes():
    x, y = pos[node]
    node_x.append(x)
    node_y.append(y)
    node_text.append(node)
    node_color.append(community_dict[node])

node_trace = go.Scatter(
    x=node_x, y=node_y,
    mode='markers',
    hoverinfo='text',
    marker=dict(
        showscale=True,
        colorscale='Viridis',
        color=node_color,
        size=10,
        colorbar=dict(
            thickness=15,
            title='Community',
            xanchor='left',
            titleside='right'
        ),
        line_width=2
    )
)
node_trace.text = node_text
fig = go.Figure(data=[edge_trace, node_trace],
             layout=go.Layout(
                title='Network graph of Reddit interactions for Blackrock Down<br>',
                titlefont_size=16,
                showlegend=False,
                hovermode='closest',
                margin=dict(b=20, l=5, r=5, t=40),
                xaxis=dict(showgrid=False, zeroline=False),
                yaxis=dict(showgrid=False, zeroline=False)
             )
)

fig.show()

/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning:

`should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.



Number of nodes: 7411
Number of edges: 13384


In [ ]:
#SENTIMENT ANALYSIS
from google.colab import files
from tqdm import tqdm
from transformers import AutoTokenizer, AutoModelForSequenceClassification
from scipy.special import softmax

MODEL = 'cardiffnlp/twitter-roberta-base-sentiment'
tokenizer = AutoTokenizer.from_pretrained(MODEL)
model = AutoModelForSequenceClassification.from_pretrained(MODEL)
df = sentimentAnalysisDf
def polarity_scores_roberta(example):
    encoded_text = tokenizer(str(example), return_tensors='pt', truncation=True, padding=True, max_length=512)
    output = model(**encoded_text)
    scores = output.logits[0].detach().numpy()
    scores = softmax(scores)
    sentiment_labels = ['negative', 'neutral', 'positive']
    scores_dict = {
        'roberta_neg': scores[0],
        'roberta_neu': scores[1],
        'roberta_pos': scores[2],
        'roberta_sentiment': sentiment_labels[scores.argmax()]
    }
    return scores_dict
results = []
for i, row in tqdm(df.iterrows(), total=len(df)):
    text = row['Text']
    roberta_result = polarity_scores_roberta(text)
    results.append(roberta_result)
df['roberta_neg'] = [result['roberta_neg'] for result in results]
df['roberta_neu'] = [result['roberta_neu'] for result in results]
df['roberta_pos'] = [result['roberta_pos'] for result in results]
df['roberta_sentiment'] = [result['roberta_sentiment'] for result in results]
output_file = '/content/sentiment_analysis_results.xlsx'
df.to_excel(output_file, index=False)
files.download(output_file)
print("Sentiment analysis completed and saved to 'sentiment_analysis_results.xlsx'.")


/usr/local/lib/python3.10/dist-packages/ipykernel/ipkernel.py:283: DeprecationWarning:

`should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:1601: FutureWarning:

`clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be depracted in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884

100%|██████████| 73251/73251 [2:53:53<00:00,  7.02it/s]


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Sentiment analysis completed and saved to 'sentiment_analysis_results.xlsx'.
